In [303]:
from google.cloud import bigquery
import os
import re
import string
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from nltk.corpus import stopwords
import nltk
import numpy as np

In [313]:
import gensim
import gensim.corpora as corpora
from gensim import models
from gensim.utils import simple_preprocess
from gensim.test.utils import common_texts
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
from gensim import similarities

In [34]:
import pandas as pd
#pd.describe_option('display')
pd.options.display.max_seq_items = 2500
pd.set_option('display.max_columns', None)  # or 1000
pd.set_option('display.max_rows', None)  # or 1000
pd.set_option('display.max_colwidth', -1)

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:6: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  


In [2]:
!pwd

/Users/ellykyles/job_match


In [3]:
os.environ['GOOGLE_APPLICATION_CREDENTIALS'] = r'/Users/ellykyles/job_match/job-match-271401-74d3c9eb9112.json'

In [193]:
query1 = '''
select *
from `job_search.job_id_list`'''

In [194]:
bq_client = bigquery.Client()

In [195]:
df = bq_client.query(query1).result().to_dataframe()

In [323]:
df.head(5)

job_id              search_first             search_latest  \
0  ea79fbd56c0915a2 2020-04-03 07:33:00+00:00 2020-04-05 23:28:00+00:00   
1  c87d828119b1396a 2020-04-02 23:27:00+00:00 2020-04-03 23:28:00+00:00   
2  8791f7605d8235f4 2020-04-01 23:29:00+00:00 2020-04-02 07:28:00+00:00   
3  0f7e71c5a5e1272b 2020-03-27 07:29:00+00:00 2020-03-27 15:28:00+00:00   
4  e07b379ce6e7ed61 2020-04-03 23:28:00+00:00 2020-04-06 07:27:00+00:00   

                                                   title  location  \
0  Personal Financial Advocate I - Banking Teller - Brea  Brea, CA   
1  Financial Advisor II                                   Mars, PA   
2  Personal Banker                                        Mesa, AZ   
3  Quantitative Financial Analyst 2                       Troy, MI   
4  Merrill Lynch Financial Advisor Development Program    Troy, MI   

                        company search_title search_location  \
0  Kinecta Federal Credit Union  Finance      Los+Angeles      
1  CITIZENS BANK                 Finance      Pittsburgh       
2  First Fidelity Bank           Finance      Phoenix          
3  Flagstar Bank                 Finance      Detroit          
4  Bank of America               Finance      Detroit          

                                             c_title second_info  counts  \
0  personal fancial advocate entry bankg teller brea  None        7        
1  fancial advisor entry                              None        3        
2  personal banker                                    None        2        
3  quantitative fancial analyst junior                None        4        
4  merrill lynch fancial advisor development program  None        6        

                                                    c_title_list  
0  [personal, financial, advocate, entry, banking, teller, brea]  
1  [financial, advisor, entry]                                    
2  [personal, banker]                                             
3  [quantitative, financial, analyst, junior]                     
4  [merrill, lynch, financial, advisor, development, program]

In [324]:
len(df['search_title'].value_counts())

24

In [325]:
# No duplicate id
duplicate_id_check=df.job_id.value_counts()
duplicate_id_check[duplicate_id_check>1]

Series([], Name: job_id, dtype: int64)

In [326]:
def mapping_job_level(text):
    text = text.replace("I", 'entry')
    text = text.replace("II", "junior")
    text = text.replace("III", 'senior')
    text = text.replace('IIII', 'senior')
    text = text.lower()
    text = text.replace(".","")
    text = text.replace("entryal","entry")
    text = text.replace("entryt", "entry")
    #text = text.replace("entryentry")
    text = text.replace('entryentry', 'entry')
    text = text.replace('entryntern', 'entry')
    #text = re.sub("[entry]+", "entry", text)
    text = text.replace("uentry", 'entry')
    text = text.replace('jr', 'junior')
    text = text.replace('juni', 'junior')
    text = text.replace('junioror','junior')
    text = text.replace('seni', 'senior')
    text = text.replace('senioror', 'senior')
    text = text.replace("csenior",'senior')
    text = text.replace('sr','senior')
    text = text.replace('sr.','senior')
    text = text.replace('2', 'junior')
    text = text.replace('3', 'senior')
    text = text.replace('4', 'senior')
    text = text.replace('5', 'senior')
    return text.strip()

In [327]:
df['c_title'] = df['title'].apply(lambda x: mapping_job_level(x))

In [328]:
nltk.download('stopwords')
stop_words = set(stopwords.words('english')) 

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/ellykyles/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [330]:
# clean the text  
def clean_text_round1(text):
    '''Make text lowercase, remove text in square brackets, remove punctuation and remove words containing numbers.'''
    text = re.sub("[-,./&–]", '', text )
    text = text.replace("staff", "")
    text = text.replace("staffing", "")
    text = text.replace("data science", "data scientist")
    text = text.replace("(", "")
    text = text.replace(")", "")
    text_list = text.split()
    text = " ".join([x for x in text_list[:8] if x not in stop_words])
    
    return text.strip()

In [350]:
df['c_title'] = df['c_title'].apply(lambda x: clean_text_round1(x))
df['counts'] = df['c_title'].str.split().str.len()

In [342]:
cv = CountVectorizer()
title_matrix = cv.fit_transform(df['c_title'].values)

title =cv.get_feature_names()
title_df = pd.DataFrame(title_matrix.sum(axis =0).T,index = title, columns =['count'] )
title_df.sort_values(by ='count', ascending = False).iloc[:200]

count
manager             14389
senior              11260
engineer            10865
analyst             6535 
developer           5842 
entry               4991 
software            4722 
assistant           4186 
sales               4029 
representative      3919 
business            3136 
specialist          3027 
data                3024 
service             2828 
product             2615 
customer            2513 
office              2272 
financial           2268 
director            2182 
account             2141 
associate           2079 
lead                1965 
development         1948 
executive           1876 
management          1774 
full                1751 
project             1748 
services            1719 
systems             1706 
operations          1656 
coordinator         1620 
technician          1614 
team                1473 
program             1440 
support             1430 
quality             1401 
consultant          1366 
accountant          1366 
agent               1289 
java                1197 
technical           1172 
time                1139 
member              1119 
scientist           1116 
designer            1088 
stack               1088 
supervisor          1070 
state               1065 
security            1023 
junior              1017 
farm                993  
administrative      973  
web                 957  
assurance           952  
medical             942  
front               906  
retail              871  
shift               855  
administrator       855  
marketing           820  
part                806  
engineering         793  
store               762  
recruiter           760  
entrynsurance       738  
architect           724  
finance             714  
general             710  
entryentry          697  
principal           675  
center              669  
maintenance         669  
level               656  
tax                 646  
application         641  
field               610  
programmer          607  
net                 604  
advisor             598  
end                 598  
cloud               569  
network             566  
accounting          564  
care                563  
officer             538  
solutions           531  
success             514  
client              507  
technology          501  
test                499  
digital             496  
rep                 483  
qa                  477  
analytics           474  
health              462  
leader              460  
professional        459  
design              456  
patient             440  
bilingual           436  
property            431  
ux                  430  
entrynformation     429  
experience          429  
outside             423  
enterprise          423  
automation          419  
clerk               415  
risk                415  
global              413  
system              411  
science             408  
banker              403  
human               400  
compliance          393  
commercial          389  
hr                  388  
nurse               385  
operator            384  
clinical            383  
regional            380  
position            379  
area                375  
devops              374  
liaison             373  
talent              370  
controller          363  
construction        358  
control             357  
restaurant          356  
training            350  
research            349  
resources           349  
production          342  
entryntelligence    337  
process             333  
personal            328  
applications        327  
mobile              327  
driver              321  
delivery            318  
ca                  312  
frontend            312  
acquisition         311  
parttime            308  
desk                305  
warehouse           302  
corporate           302  
auditor             297  
tech                295  
partner             295  
backend             293  
electrical          288  
pharmacy        

In [343]:
df['c_title'].value_counts()     #data scientist  

customer service representative                                                                                      460
executive assistant                                                                                                  375
accountant                                                                                                           368
senior software engineer                                                                                             366
software engineer                                                                                                    346
office manager                                                                                                       265
business analyst                                                                                                     230
administrative assistant                                                                                             229
senior accountant               

In [344]:
df['c_title_list'] = df['c_title'].str.split()
title_list=df['c_title_list'].tolist()

In [336]:
import gensim
import gensim.corpora as corpora
from gensim import models
from gensim.utils import simple_preprocess
from gensim.test.utils import common_texts
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
from gensim import similarities

In [345]:
gensim_dictionary = corpora.Dictionary(title_list)
for k, v in gensim_dictionary.token2id.items():
    print(f'{k:{15}} {v:{10}}')

advocate                 0
banking                  1
brea                     2
entry                    3
financial                4
personal                 5
teller                   6
advisor                  7
banker                   8
analyst                  9
junior                  10
quantitative            11
development             12
lynch                   13
merrill                 14
program                 15
aml                     16
accounting              17
director                18
entrynformation         19
finance                 20
senior                  21
technolo                22
center                  23
lending                 24
officerdoral            25
services                26
specialist              27
consumer                28
developmen              29
entrynvestments         30
solutions               31
cfohinsdalela           32
grange                  33
actuarial               34
pharmacy                35
psseniorsenior77junior      

profiles              1954
manageme              1955
fprh                  1956
skilled               1957
uniquely              1958
experienc             1959
8th                   1960
magnolia              1961
surrounding           1962
firms                 1963
search                1964
downer                1965
ecom                  1966
july                  1967
privatebusiness       1968
women's               1969
supervision           1970
physician             1971
expertsenior          1972
mcmc                  1973
media                 1974
rqentry               1975
challenge             1976
servicesbanking       1977
fern                  1978
locations             1979
centralized           1980
eq                    1981
refinancehome         1982
stock                 1983
analystdod            1984
rccb                  1985
gtm                   1986
cphrm                 1987
contingent            1988
programmatic          1989
dunwoody              1990
g

jslead                3579
react                 3580
richfield             3581
midnight              3582
capa                  3583
seniorquality         3584
pharmaceutical        3585
preda                 3586
uas                   3587
tool                  3588
qat                   3589
managerquality        3590
specialistdata        3591
cseniors              3592
trial                 3593
directorate           3594
evaluation            3595
sesenior              3596
te                    3597
nsqentryp             3598
airline               3599
cyberspace            3600
role                  3601
visa                  3602
uat                   3603
hospice               3604
analystentrynspector       3605
brownsboro            3606
norton                3607
outcomes              3608
analystassociate       3609
7:00am                3610
mulesoft              3611
analystsenior1senior7       3612
arborist              3613
curam                 3614
entrybm         

demand                4953
arcgentrys            4954
locatext              4955
digitalux             4956
authentication        4957
managerchicago        4958
securit               4959
designerprint         4960
connected             4961
alt                   4962
designerjuniorsenior       4963
requir                4964
working               4965
junior0junior0seniorsenior       4966
appweb                4967
connectors            4968
amerilife             4969
wizard                4970
entryxd               4971
0juniorjunior0junior0senior188senior       4972
humancentered         4973
entryncredible        4974
uxentryart            4975
managerfront          4976
designerauthor        4977
architectentryntermediate       4978
generalistseniord       4979
detectionaml          4980
webuxentry            4981
designerapplications       4982
experiencevisual       4983
zsystems              4984
bringing              4985
join                  4986
killer                4987


1+yrs                 6952
plaintiff’s           6953
followup              6954
asssistant            6955
{s0junior18seniorp}       6956
{s0junior190p}        6957
scripted              6958
series                6959
coordinatormedical       6960
showroom              6961
mercy                 6962
managerbookkeeperadministrative       6963
pksenior              6964
salaried              6965
manageroffice         6966
hou                   6967
11b                   6968
entrynfantryman       6969
biologics             6970
conciergereceptionist       6971
paralegaladministrative       6972
uni                   6973
holderassistant       6974
assistantproject       6975
dundalk               6976
salon                 6977
stylist               6978
coordinatorreal       6979
summit's              6980
money                 6981
acco                  6982
billercollector       6983
galleria              6984
dispatcheroffice       6985
qsenior               6986
reventrysed*rese

devopssoftware        8952
electromechanentrycal       8953
mask                  8954
pmentryc              8955
multimediacamera       8956
controllersubsystem       8957
qara                  8958
entrysseentrysso       8959
mmentryp              8960
uee                   8961
highwaybridge         8962
ds                    8963
gs                    8964
utentrylentryy        8965
engineer;             8966
scripting             8967
:java                 8968
09senior9juniorsenior       8969
1senior+              8970
tentrym               8971
dmr                   8972
sdentryrt             8973
wpoly                 8974
tentryer              8975
missile               8976
developmentapplication       8977
hpcdev                8978
particle              8979
fermentation          8980
engineership          8981
catv                  8982
juliet                8983
analystmt             8984
laurel                8985
entrydea              8986
pflugerville          8987
pec

asl                  10951
senior0junior        10952
entryconcord         10953
pba                  10954
buyerplanner         10955
*entrymmed           10956
echocardiographer      10957
descvoanurse         10958
blend                10959
cath                 10960
catheterization      10961
groceryfreight       10962
cart                 10963
17c                  10964
asos                 10965
caf                  10966
staneval             10967
17e                  10968
91l                  10969
9juniorr             10970
parachute            10971
rigger               10972
transportationlogistics      10973
chat!                10974
seniorjuniorjunior6      10975
coordinatorfair      10976
tube                 10977
tl                   10978
emtb                 10979
cdlamaterial         10980
seniorseniorjunior      10981
correctio            10982
tanfncp              10983
springwater          10984
prenatal             10985
fill                 10986
finish     

janentryor           12951
{oncall}             12952
romulus              12953
dm                   12954
namer                12955
gs0senior1808        12956
morrison             12957
clear                12958
utmb                 12959
kansaswester         12960
entrynsouthern       12961
miss                 12962
aidenew              12963
ratesapply           12964
yardley              12965
bookkeepercredit      12966
hentryv              12967
nentryaentrydlmm      12968
klp                  12969
coney                12970
sourcin              12971
psseniorjunior80senior      12972
[                    12973
raw                  12974
conferences          12975
callentryng          12976
prohibited           12977
hrly                 12978
supermarket          12979
dispatcherpolice      12980
accredo              12981
ohana                12982
atlas                12983
mandarinchinese      12984
rim                  12985
entry600senior       12986
leisure           

psseniorjunior776      14950
recording            14951
mem                  14952
retail66seniorsenior      14953
6:senior0amsenior:000      14954
regentrystratentryon      14955
arrc                 14956
birth                14957
nams                 14958
stockroom            14959
offpremise           14960
wineliquor           14961
specialistannapolis      14962
mseniorsenior        14963
jjunior              14964
ednor                14965
juniorseniorjuniorsenior      14966
shuttle              14967
harrison             14968
brookline            14969
msenior06            14970
10:1seniorpm6:1senioram      14971
situate              14972
porsche              14973
nonunion             14974
occasions            14975
laundrydayevening      14976
techuh               14977
uxa19senior09        14978
juniorsenior61       14979
unlimited            14980
annuities            14981
clevelandpittsburgh      14982
tellercustomer       14983
deer                 14984
entrynplan

In [346]:
corpus = [gensim_dictionary.doc2bow(line) for line in np.array(title_list)]
documents = [TaggedDocument(doc, [i]) for i, doc in enumerate(df['c_title_list'])]

In [347]:
lsi = models.LsiModel(corpus, id2word = gensim_dictionary, num_topics = 20)
index = similarities.MatrixSimilarity(lsi[corpus])

In [352]:
vec_bow= gensim_dictionary.doc2bow('data scientist'.split())
vec_lsi = lsi[vec_bow]
sims = index[vec_lsi]
item_index = np.argsort(sims)[::-1]
df.iloc[item_index[:10]][["job_id","title"]]

job_id                    title
25704  a718ded1edca09d3  Data Scientist         
27037  0ed412cc0aa9254a  Data Scientist         
26273  b064f411b15706cf  E-09-311 Data Scientist
26693  d47f6e43c7e449fe  Data Scientist         
26272  720445df45b60490  Data Scientist         
57420  e97c3225cc89ca16  Data Scientist         
26689  14994bde8b3f6cd8  Data Scientist         
36954  71f1dcf70a9ff4a5  Data Scientist         
26382  7b97a318bd40dc1f  Data Scientist         
26836  6b7d4d5e5a84cdac  Data Scientist

In [353]:
vec_bow= gensim_dictionary.doc2bow('full developer'.split())
vec_lsi = lsi[vec_bow]
sims = index[vec_lsi]
item_index = np.argsort(sims)[::-1]
df.iloc[item_index[:10]][["job_id","title"]]

job_id  \
59036  58dee3185e37274c   
57758  1699f0dff1837246   
20042  62682b074f061048   
59275  00aa2ce81f0602aa   
60161  aad78707766007f1   
65543  43ea594f3c56463e   
56659  bbb99c7118cc78a9   
18595  d9a60b4e2aa69018   
19916  53bc9df5bf5b8cb7   
64533  8968a8d6fdf81af4   

                                                                 title  
59036  Full Stack/ADF Developer need in Alpharetta, GA                  
57758  Full stack/Java/J2EE developer, Tysons, VA                       
20042  Full Cycle Web Developer                                         
59275  Java Full Stack/Angular Developer                                
60161  .Net Full Stack Developer - C#, .Net, .NET Core, Spring, Hib...  
65543  Full Stack .NET Web Developer                                    
56659  Full Stack .NET Web Developer                                    
18595  Full Stack .NET Developer - .NET Core, Angular4 +, Angular 6...  
19916  Full Stack Web Developer - Java Spring Framework with SQL Se...  
64533  Full Stack Web Application Developer